In [1]:
from tqdm import tqdm
from sentence_transformers import SentenceTransformer, util

D:\Projects\LLMs\venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# model = SentenceTransformer('DMetaSoul/sbert-chinese-general-v2')
model = SentenceTransformer('TintinMeimei/menglang_yongtulv_aimatch_v1')

In [3]:
def sim(text1, text2):
    emb1 = model.encode(text1, convert_to_tensor=True)
    emb2 = model.encode(text2, convert_to_tensor=True)
    score = util.cos_sim(emb1, emb2)
    return score

In [24]:
text1 = '挂机空调'
# text2 = '1.1.11 高效节能家用电器制造\n包括节能型房间空调器、空调机组、电冰箱、电动洗衣机、平板电视机、电风扇等家用电器制造。房间空气调节器能效优于《房间空气调节器能效限定值及能效等级》（GB 12021.3）标准1级能效水平；转速可控型房间空气调节器能效优于《转速可控型房间空气调节器能效限定值及能效等级》（GB 21455）标准1级能效水平；多联式空调（热泵）机组能效比优于《多联式空调（热泵）机组能效限定值及能源效率等级》（GB 21454）标准1级能效水平；家用电冰箱能效优于《家用电冰箱耗电量限定值及能效等级》（GB 12021.2）标准1级能效水平；电动洗衣机能效优于《电动洗衣机能效水效限定值及等级》（GB 12021.4）标准1级能效水平；电饭煲能效优于《电饭锅能效限定值及能效等级》（GB 12021.6）标准1级能效水平；平板电视机能效优于《平板电视能效限定值及能效等级》（GB 24850）标准1级能效水平；交流电风扇能效优于《交流电风扇能效限定值及能效等级》（GB 12021.9）标准1级能效水平。其他高效节能家用电器能效均优于相应国家强制性标准1级能效水平。'
# text2 = '包括节能泵、节能型真空干燥设备、节能型真空炉等设备制造。清水离心泵能效指标优于《清水离心泵能效限定值及节能评价值》（GB 19762）标准中节能评价值水平；石油化工离心泵能效优于《石油化工离心泵能效限定值及能效等级》（GB 32284）标准中1级能效水平；潜水电泵能效优于《井用潜水电泵能效限定值及能效等级》（GB 32030）、《小型潜水电泵能效限定值及能效等级》（GB 32029）、《污水污物潜水电泵能效限定值及能效等级》（GB 32031）标准中1级能效水平。'
text2 = '退耕还林'

In [25]:
sim(text1, text2)

tensor([[-0.5000]], device='cuda:0')

### Process Data

In [6]:
import pandas as pd

df_data = pd.read_excel('AI匹配算法样本.xlsx', sheet_name='Sheet1', dtype=str)
df_data.head(2)

X1                                                 X2  \
0  中新制药厂空调末端送回风系统改造-询价公示  1.1.11 高效节能家用电器制造\n包括节能型房间空调器、空调机组、电冰箱、电动洗衣机、平...   
1  中新制药厂空调末端送回风系统改造-询价公示  1.5.1 锅炉（窑炉）节能改造和能效提升\n包括燃煤锅炉“以大代小”，采用先进燃煤锅炉、节...   

   Y  Split  
0  1  train  
1  0  train

In [7]:
train_data = [item for item in df_data.to_dict(orient='record') if item['Split']=='train']
eval_data = [item for item in df_data.to_dict(orient='record') if item['Split']=='eval']
test_data = [item for item in df_data.to_dict(orient='record') if item['Split']=='test']

C:\Users\vermouth\AppData\Local\Temp\ipykernel_22160\3257358016.py:1: FutureWarning: Using short name for 'orient' is deprecated. Only the options: ('dict', list, 'series', 'split', 'records', 'index') will be used in a future version. Use one of the above to silence this warning.
  train_data = [item for item in df_data.to_dict(orient='record') if item['Split']=='train']
C:\Users\vermouth\AppData\Local\Temp\ipykernel_22160\3257358016.py:2: FutureWarning: Using short name for 'orient' is deprecated. Only the options: ('dict', list, 'series', 'split', 'records', 'index') will be used in a future version. Use one of the above to silence this warning.
  eval_data = [item for item in df_data.to_dict(orient='record') if item['Split']=='eval']
C:\Users\vermouth\AppData\Local\Temp\ipykernel_22160\3257358016.py:3: FutureWarning: Using short name for 'orient' is deprecated. Only the options: ('dict', list, 'series', 'split', 'records', 'index') will be used in a future version. Use one of the a

### Model 1 - Fine tune a Sentence Transformer

In [8]:
# from sentence_transformers import InputExample, losses
# from torch.utils.data import DataLoader

# # Prepare data
# train_data_sbert = []
# eval_data_sbert = []
# test_data_sbert = []

# for item in train_data:
#     label = 1.0 if float(item.get('Y')) == 1 else -1.0
#     train_data_sbert.append(InputExample(texts=[item.get('X1'), item.get('X2')], label=label))
# train_dataloader = DataLoader(train_data_sbert, shuffle=True, batch_size=2)
# train_loss = losses.CosineSimilarityLoss(model)

In [9]:
# from sentence_transformers import evaluation
# evaluator = evaluation.EmbeddingSimilarityEvaluator([item.get('X1') for item in eval_data], [item.get('X2') for item in eval_data], [1.0 if float(item.get('Y'))==1 else -1.0 for item in eval_data])

In [10]:
# model.fit(train_objectives=[(train_dataloader, train_loss)], epochs=1, warmup_steps=100, evaluator=evaluator, evaluation_steps=500)

In [11]:
# model.save('./tmp_model')

### Model 2 - No Fine Tune + Threshold Tuning

In [12]:
def sim(text1, text2):
    emb1 = model.encode(text1, convert_to_tensor=True)
    emb2 = model.encode(text2, convert_to_tensor=True)
    score = util.cos_sim(emb1, emb2)
    return score

def _acc_thres(scores, thres):
    correct = 0
    total = len(scores)
    for score, truth in scores:
        truth = float(truth)
        pred = 1 if score >= thres else 0
        if pred == truth:
            correct += 1
    return round(correct/total, 3)

def model_train(train_data, eval_data):
    score_train = []
    score_eval = []
    for item in tqdm(train_data):
        score = sim(item['X1'], item['X2'])
        score_train.append((score, item['Y']))
    for item in tqdm(eval_data):
        score = sim(item['X1'], item['X2'])
        score_eval.append((score, item['Y']))
    # find threshold that minize train error
    score_train = sorted(score_train, reverse=True)
    win_acc = -1
    win_thres = -1
    for thres in range(5, 100, 5):
        thres = thres*0.01
        acc = _acc_thres(score_train, thres)
        if acc > win_acc:
            win_acc = acc
            win_thres = thres
    eval_acc = _acc_thres(score_eval, win_thres)
    return {'thres': win_thres, 'train_accuracy': win_acc, 'eval_accuracy': eval_acc}

In [13]:
r = model_train(train_data, eval_data)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4248/4248 [04:44<00:00, 14.94it/s]


In [14]:
r

{'thres': 0.25, 'train_accuracy': 0.831, 'eval_accuracy': 0.816}

In [15]:
score_test = []
for item in tqdm(test_data):
    score = sim(item['X1'], item['X2'])
    score_test.append((score, item['Y']))

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4468/4468 [04:58<00:00, 14.98it/s]


In [17]:
_acc_thres(score_test, r['thres'])
#_acc_thres(score_test, 0.25)

0.815